In [1]:
# procedure for calculating hydraulic confinement along a pressure tunnel 
# completed procedure will in the form of a design report
#   safety factor against hydraulic confinement calculated at stationed points along tunnel alignment
#   calculation determines the minimum dstance from the stationed point to the terrain surface 

# project name: 'Snow Mountain 2.0 PSP' 

In [2]:
# ToDo
#   DONE need to read in 'slope' and get slope values for all buffer grid points 'MIN'
#   DONE Nam Ang headrace tunnel alignment and DTM
#   DONE add calculation for hydraulic confinement safety factor (SF)
#   DONE add results plot for hydraulic confinement safety factor
#   put common functions (e.g. setup, data format conversions) into a separate module/API
#   DONE use Nam Ang HEP data for initial testing and demo
#   provide full desgin criteria text in Jupyter Notebook design report
#   DONE add check plot with alignment, station points, buffer points
#   DONE add check plot with MIN buffer grid points
#   refactor code

In [3]:
# import required python libraires
import numpy as np
from numpy import *
import pandas as pd
import geopandas as gpd
import shapely as sp
#import matplotlib.pylab as pylab  #matplotlib not currently used
#import matplotlib.pyplot as plt
#%matplotlib inline

# testing
#import random
# check pd and gpd version
#print(pd.__version__)
#print(gpd.__version__)

In [4]:
# python setup for qgis processing
import sys, os
from qgis.core import QgsApplication
from PyQt4.QtGui import QApplication
app = QApplication([], True)  #True -> window display enabled
QgsApplication.setPrefixPath("/usr", True)
QgsApplication.initQgis()
sys.path.append('/usr/share/qgis/python/plugins')  #export PYTHONPATH not needed in start script
from processing.core.Processing import Processing
Processing.initialize() 
import processing
#from processing.tools import *  #not needed currently

In [5]:
# set up plotly in 'offline' mode                            #ToDo JK: this should be cleaned up and documented
from plotly import __version__
from plotly.offline import download_plotlyjs, init_notebook_mode, plot,iplot
import plotly.graph_objs as go
init_notebook_mode(connected=True)
print (__version__) # requires version >= 1.9.0

# collect all plotly setups here
import plotly.offline as plotly
from plotly.graph_objs import *

2.2.1


In [6]:
# import DSS modules
#import geospatial as geo

In [7]:
# set wd for this procedure and project 
os.chdir("/home/kaelin_joseph/DSS.HydraulicConfinement/")

In [8]:
# set maximum number of rows to display from a pandas data frame
#pd.set_option('display.max_rows', 3000)
pd.set_option('display.max_rows', 30000)

In [9]:
# define required input files
# Snowy Mountain 2.0 PSP
# D/S PH, vertical shaft waterways alignment
# alignment data will be defined direclty in Jupyter Notebook, to better document alternatives studied
##Alignment = "data/in/SnowMountains2.WaterwaysAlignment.r2.csv"  
DTM = "data/in/SnowyMountainsTopogRaster.tif"  #DEM with surface topography
#   Alignment contains fields "Point","Type","Station","Northing","Easting","Elevation"
#   check Alignment data: no spaces between comma-separated fields
#   check Alignment data: no trailing blank lines, no duplicate lines
DTM_slope='data/in/SnowyMountainsSlopeRaster.tif'  #DEM containing slope angle as attribute

In [10]:
# Following alignments approximate vertical shaft by adding a small inclination
# Procedure should be adapted to calculate sloped chainage separately and using this for calculations  #ToDo JK


In [11]:
# Snowy Mountain 2.0 PSP
# study of alternative layouts / alignments

In [12]:
# # JV Ravine Option (U/S PH, vertical shaft)
# # 'Waterway _ Alignment and Invert Profile_Original Design and Alt 1 & 2_Ex....xlsx' 
# #  received 2018.05.02. M. Bieir
# #  Alignment data is from Civil3d and is rigidly output at 50 m station intervlas,
# #  not at alignment tangent points. E.g. vertical shaft is therefore not vertical.
# alignment = {
#     'Station':[17000.00, 17600.00, 17590.00, 17500.00, 18200.00], 
#     'Northing':[6038550.513, 6038110.759, 6038100.759, 6038082.846, 6038217.433],
#     'Easting':[632542.222, 632134.091, 632120.091, 632092.765, 631575.465],
#      #elevations in data are for tunnel invert, elevations adjusted for +4.5m for 9m tunnel diameter 
#     'Elevation':[1106.183, 1105.800, 980.800, 449.500, 446.629]
#     }

In [13]:
# # JV Alt 2 (D/S PH, vertical shaft)
# # 'Waterway _ Alignment and Invert Profile_Original Design and Alt 1 & 2_Ex....xlsx' 
# #  received 2018.05.02. M. Bieir
# #  Alignment data is from Civil3d and is rigidly output at 50 m station intervlas,
# #  not at alignment tangent points. E.g. vertical shaft is therefore not vertical.
# alignment = {
#     'Station':[18500.0, 19400.0, 19650.0, 19700.0, 20+150.0],
#     'Northing':[6038594.951,6038611.442,6038458.908,6038422.009,6038135.211],
#     'Easting':[631021.964,630122.473,629930.936,629897.196,629563.649],
#      #elevations in data are for tunnel invert, elevations adjusted for +4.5m for 9m tunnel diameter 
#     'Elevation':[1078.121,1076.866,1076.518,438.769,421.364]
#     }

In [14]:
# # JV JV1 2018.05.15 (vertical shaft)
# # Snowy_Concept_Check for Confinement_2018 05 15.xlsx received 2018.05.15 from M. Bieri
# alignment = { 
#     'Station':[16956, 19348.7, 19512.6, 19512.6, 19512.6, 19512.6, 19512.6, 19512.6, 19512.6, 19602, 19608],
#     'Northing':[6038616.024, 6038680.380, 6038684.787, 6038684.787, 6038684.787, 6038684.787, 6038684.787, 
#                 6038684.787, 6038684.787, 6038687.191, 6038687.358],
#     'Easting':[632522.964, 630130.630, 629966.831, 629965.831, 629964.831, 629963.831, 
#                629962.831, 629961.831, 629960.831, 629877.463, 629871.245],
#     #elevations in data are for tunnel invert
#     #'Elevation':[1101.00, 1097.51, 1081.12, 1000.0, 900.0, 800.0, 700.0, 600.0, 448.94, 440.00, 432.00]
#     #elevations adjusted for +5.0m for 10m tunnel diameter
#     'Elevation':[1106.00, 1102.51, 1086.12, 1000.0, 900.0, 800.0, 700.0, 600.0, 453.94, 445.00, 437.00]
#     }

In [15]:
# # JV JV2 2018.05.15 (vertical shaft)
# # Snowy_Concept_Check for Confinement_2018 05 15.xlsx received 2018.05.15 from M. Bieri
# alignment = { 
#     'Station':[8606, 16956, 16956, 16956, 16956, 16956, 16956, 16956, 19512.6, 19602, 19608],
#     'Northing':[6038391.483, 6038616.024, 6038616.024, 6038616.024, 6038616.024, 6038616.024, 6038616.024, 
#                 6038616.024, 6038684.787, 6038687.191, 6038687.358],
#     'Easting':[640869.945, 632522.964, 632521.964, 632520.964,  632519.964,  632518.964,  632517.964, 
#                632516.964, 629966.831, 629877.463, 629871.245],
#     #elevations in data are for tunnel invert
#     #'Elevation':[1122.84, 1101.00, 1000.0, 900.0, 800.0, 700.0, 600.0, 448.94, 448.94, 440.00, 432.00]        
#     #elevations adjusted for +5.0m for 10m tunnel diameter    
#     'Elevation':[1127.84, 1106.00, 1000.0, 900.0, 800.0, 700.0, 600.0, 453.94, 453.94, 445.00, 437.00]    
#     }

In [16]:
# #JV JV3 2018.05.15 (inclined shaft)
# # Snowy_Concept_Check for Confinement_2018 05 15.xlsx received 2018.05.15 from M. Bieri
# alignment = { 
#     'Station':[16956, 17005.5, 19262.6, 19512.6, 19602, 19608],
#     'Northing':[6038616.024, 6038616.024, 6038680.380, 6038684.787, 6038687.191, 6038687.358], 
#     'Easting':[632522.964, 632472.964, 630216.831, 629966.831, 629877.463, 629871.245 ],
#     #elevations in data are for tunnel invert
#     #'Elevation':[1101.00, 1097.51, 448.94, 448.94, 440.00, 432.00]
#     #elevations adjusted for +5.0m for 10m tunnel diameter        
#     'Elevation':[1106.00, 1102.51, 453.94, 453.94, 445.00, 437.00]
#     }

In [17]:
# # RTF-1 2018.05.11
# # S2-8200-DRG-XXXXXX Power Waterway Release 1.pdf, 2018.05.11 from F. Takhtemina
# alignment = { 
#     'Station':[15000.0, 16886.428, 17081.8, 17082.8, 17083.8, 17084.8, 17085.8, 18081.8],
#     'Northing':[6038473.48, 6038513.415, 6038547.365, 6038547.365, 6038547.365, 6038547.365, 
#                 6038547.365, 6038721.013],    
#     'Easting':[634520.11, 632634.103, 632441.519, 632440.519, 632439.519, 632438.519, 
#                632437.519, 631456.711], 
#     #elevations in data are for tunnel invert
#     #'Elevation':[1103.9, 1101.1, 1095.0, 1000.0, 800.0, 650.0, 546.2, 448.0]
#     #elevations adjusted for +5.0m for 10m tunnel diameter            
#     'Elevation':[1108.9, 1106.1, 1100.0, 1000.0, 800.0, 650.0, 551.2, 453.0]
# }

In [18]:
# JV JV1 2018.05.17 (400 m vertical shaft, longer 10% LPT)
# S2-TD-DRG-RFT_JV1&3 ALT-PP- SHEET 1  received 2018.05.15 from M. Bieri
alignment = { 
    'Station':[15000, 17271.925, 17271.925, 19726.777],
    'Northing':[6038563.42, 6038624.52, 6038624.52, 6038690.53], 
    'Easting':[634478.26, 632207.15, 632206.15, 629753.18],
    #elevations in data are for tunnel invert
    #'Elevation':[1106.11, 1100.17, 685.485, 440.0] 
    #elevations adjusted for +5.0m for 10m tunnel diameter                
    'Elevation':[1111.11, 1105.17, 690.485, 445.0] 
    }

In [19]:
# define required input data

# mapping
crs = {'init': 'epsg:32755'}  #define crs for project Snowy Mountains 2
grass_region = "619000,656000,6029000,6043000"  #map region E1,E2,N1,N2 Snowy Mountains 2

# resolution for analysis
#grass_station_dist = 20  #use for high resolution
grass_station_dist = 50  #use for low resolution
c = 0.5  #ring buffer radius = c*h  (h=overburden)
#res = 3.0  #use for high resolution
res = 25.0  #use for low resolution

# rock properties
density_rock = 27.0  #kN/m3

# hydraulic properties
# upsurge varies along HRT and should be defined as a function                                       #Todo JK
max_static_water_level = 1228.7 + 70  #MASL, include upsurge
print(max_static_water_level)

start_station = alignment['Station'][0]  ####
print(start_station)

1298.7
15000


In [20]:
alignment_df = pd.DataFrame(alignment)
alignment_df = alignment_df[['Station','Northing','Easting','Elevation']]  #for checking

In [21]:
# define temporary data
Alignment_shp ='tmp/SnowyMtn2Alignment.shp'  #alignment shp from Alignment
Alignment_grass_csv = 'tmp/SnowyMtn2AlignmentGrass.csv'  #alignment csv fixed for grass
Alignment_line_shp = "tmp/SnowyMtn2AlignmentLine.shp"  #intermediate data
Alignment_stationed_shp = "tmp/SnowyMtn2AlignmentStationed.shp"  #alignment shp containing station points
Alignment_dtm_csv = "tmp/SnowyMtn2AlignmentDTM.csv"  #alignment including terrain elevations at station points
Buffer_shp = "tmp/SnowyMtn2Buffer.shp"  #buffer shp containing ring grid points at a particular station point
Buffer_all_csv = "tmp/SnowyMtn2BufferAll.csv"  # all station point ring buffers written to csv
Buffer_all_shp = "tmp/SnowyMtn2BufferFinal.shp"
Buffer_dtm_csv = "tmp/SnowyMtn2BufferDTM.csv"
Buffer_slope_csv = "tmp/SnowyMtn2BufferSlope.csv"

In [22]:
# define output files


In [23]:
# for Snowy Mountain 2.0 PSP, data will be defined in Jupyter Notebook, to better document alternatives studied
# # create alignment_df (dataframe) from Alignment csv                     #ToDo JK: make into csv -> df function
# alignment_df = pd.read_csv(Alignment)

# # delete row if only NA are present in row
# alignment_df = alignment_df.dropna(how = "all")
# # round alignment_df to three decimals
# alignment_df = alignment_df.round(decimals=3)

In [24]:
alignment_df

Station    Northing    Easting  Elevation
0  15000.000  6038563.42  634478.26   1111.110
1  17271.925  6038624.52  632207.15   1105.170
2  17271.925  6038624.52  632206.15    690.485
3  19726.777  6038690.53  629753.18    445.000

In [25]:
# create stationed alignment as Alignment_stationed_shp                 #ToDo JK: make into stationing function
# from points in alignment_df
#   required grass input data: x, y coordinates at each alignment point
#   grass input for function v.in.line 1) must have x first and y second; 2) no header 
#   grass output: x, y coordinates at each station point along alignment
alignment_df_grass = alignment_df.loc[:,["Easting", "Northing"]]  #x first and y second
# write Alignment_grass_csv
alignment_df_grass.to_csv(Alignment_grass_csv, header=False, index=False)  #no header

# points to line, write output to Alignment_line_shp
processing.runalg("grass7:v.in.lines",Alignment_grass_csv,",",False,
                  grass_region,0,Alignment_line_shp)  #no spaces between commas

# line to station points, ouput segmented polyline to Alignment_stationed_shp
processing.runalg("grass7:v.to.points",Alignment_line_shp,grass_station_dist,1,True,
                  grass_region,-1,0.0001,0,Alignment_stationed_shp)  #no spaces between commas

{'output': 'tmp/SnowyMtn2AlignmentStationed.shp'}

In [26]:
# create alignment_stationed_df from Alignment_stationed_shp            #ToDo JK: make into shp -> df function
#   required output data: x_align, y_align at each station point
alignment_stationed_df = gpd.read_file(Alignment_stationed_shp)

# create columns for x_align, y_align, then delete columns cat_ and geometry
alignment_stationed_df["x_align"] = alignment_stationed_df.geometry.x
alignment_stationed_df["y_align"] = alignment_stationed_df.geometry.y
alignment_stationed_df = alignment_stationed_df.drop(columns =["cat_", "geometry"])

In [27]:
#alignment_stationed_df

In [28]:
# add required fields to alignment_stationed_df

# add "id" 
alignment_stationed_df["id_point"] = alignment_stationed_df.index

# add "distance_stat" referencing length between point n and point n+1
#   is this what is intended??                                                                       ToDo: JK
alignment_stationed_df["distance_stat"] = np.nan
for n in range(0, len(alignment_stationed_df)-1):
    alignment_stationed_df.iloc[n, alignment_stationed_df.columns.get_loc("distance_stat")] = (
        ((alignment_stationed_df.iloc[n +1]["x_align"] - alignment_stationed_df.iloc[n]["x_align"])**2
        +(alignment_stationed_df.iloc[n +1]["y_align"] - alignment_stationed_df.iloc[n]["y_align"])**2 )**(0.5) )

# add "distance_stat_sum"
alignment_stationed_df["distance_stat_sum"] = np.nan
alignment_stationed_df.iloc[0, alignment_stationed_df.columns.get_loc("distance_stat_sum")] = start_station  ####
####for n in range(1, len(alignment_stationed_df) -1):
for n in range(1, len(alignment_stationed_df)):  #refactor !!!
    ####distance = ( alignment_stationed_df.loc[(alignment_stationed_df.id_point.isin(range(0,n +1))), 
    ####                    "distance_stat"] )
    distance = ( alignment_stationed_df.loc[(alignment_stationed_df.id_point.isin(range(0,n))), 
                        "distance_stat"] )
    distances = distance.tolist()
    alignment_stationed_df.iloc[n, alignment_stationed_df.columns.get_loc("distance_stat_sum")] = (
                                                                               sum(distances) +start_station)
    
#alignment_stationed_df.head()
alignment_stationed_df

x_align       y_align  id_point  distance_stat  distance_stat_sum
0   634478.260000  6.038563e+06         0       49.38982       15000.000000
1   634428.888043  6.038565e+06         1       49.38982       15049.389820
2   634379.516087  6.038566e+06         2       49.38982       15098.779641
3   634330.144130  6.038567e+06         3       49.38982       15148.169461
4   634280.772174  6.038569e+06         4       49.38982       15197.559282
5   634231.400217  6.038570e+06         5       49.38982       15246.949102
6   634182.028261  6.038571e+06         6       49.38982       15296.338923
7   634132.656304  6.038573e+06         7       49.38982       15345.728743
8   634083.284348  6.038574e+06         8       49.38982       15395.118564
9   634033.912391  6.038575e+06         9       49.38982       15444.508384
10  633984.540435  6.038577e+06        10       49.38982       15493.898205
11  633935.168478  6.038578e+06        11       49.38982       15543.288025
12  633885.796522  6.038579e+06        12       49.38982       15592.677846
13  633836.424565  6.038581e+06        13       49.38982       15642.067666
14  633787.052609  6.038582e+06        14       49.38982       15691.457487
15  633737.680652  6.038583e+06        15       49.38982       15740.847307
16  633688.308696  6.038585e+06        16       49.38982       15790.237128
17  633638.936739  6.038586e+06        17       49.38982       15839.626948
18  633589.564783  6.038587e+06        18       49.38982       15889.016769
19  633540.192826  6.038589e+06        19       49.38982       15938.406589
20  633490.820870  6.038590e+06        20       49.38982       15987.796410
21  633441.448913  6.038591e+06        21       49.38982       16037.186230
22  633392.076957  6.038593e+06        22       49.38982       16086.576051
23  633342.705000  6.038594e+06        23       49.38982       16135.965871
24  633293.333043  6.038595e+06        24       49.38982       16185.355692
25  633243.961087  6.038597e+06        25       49.38982       16234.745512
26  633194.589130  6.038598e+06        26       49.38982       16284.135333
27  633145.217174  6.038599e+06        27       49.38982       16333.525153
28  633095.845217  6.038601e+06        28       49.38982       16382.914974
29  633046.473261  6.038602e+06        29       49.38982       16432.304794
30  632997.101304  6.038603e+06        30       49.38982       16481.694615
31  632947.729348  6.038605e+06        31       49.38982       16531.084435
32  632898.357391  6.038606e+06        32       49.38982       16580.474256
33  632848.985435  6.038607e+06        33       49.38982       16629.864076
34  632799.613478  6.038609e+06        34       49.38982       16679.253897
35  632750.241522  6.038610e+06        35       49.38982       16728.643717
36  632700.869565  6.038611e+06        36       49.38982       16778.033538
37  632651.497609  6.038613e+06        37       49.38982       16827.423358
38  632602.125652  6.038614e+06        38       49.38982       16876.813178
39  632552.753696  6.038615e+06        39       49.38982       16926.202999
40  632503.381739  6.038617e+06        40       49.38982       16975.592819
41  632454.009783  6.038618e+06        41       49.38982       17024.982640
42  632404.637826  6.038619e+06        42       49.38982       17074.372460
43  632355.265870  6.038621e+06        43       49.38982       17123.762281
44  632305.893913  6.038622e+06        44       49.38982       17173.152101
45  632256.521957  6.038623e+06        45       49.38982       17222.541922
46  632207.150000  6.038625e+06        46        1.00000       17271.931742
47  632206.150000  6.038625e+06        47       49.07716       17272.931742
48  632157.090600  6.038626e+06        48       49.07716       17322.008903
49  632108.031200  6.038627e+06        49       49.07716       17371.086063
50  632058.971800  6.038628e+06        50       49.07716       17420.163223
51  632009.912400  6.038630e+06        51       49.07716  

In [29]:
# add required field "distance_intermed_align" to alignment_df
alignment_df["distance_intermed_align"] = np.nan

for n in range(0, len(alignment_df) -1):
    alignment_df.iloc[n, alignment_df.columns.get_loc("distance_intermed_align")] = (
        ((alignment_df.iloc[n +1]["Easting"]-alignment_df.iloc[n]["Easting"])**2 
             +(alignment_df.iloc[n +1]["Northing"]-alignment_df.iloc[n]["Northing"])**2 )**(0.5) )
    
#alignment_df.head()
alignment_df

Station    Northing    Easting  Elevation  distance_intermed_align
0  15000.000  6038563.42  634478.26   1111.110              2271.931742
1  17271.925  6038624.52  632207.15   1105.170                 1.000000
2  17271.925  6038624.52  632206.15    690.485              2453.858012
3  19726.777  6038690.53  629753.18    445.000                      NaN

In [30]:
# join alignment_df to alignment_stationed_df
alignment_stationed_df = pd.merge(left= alignment_stationed_df, right = alignment_df, 
                 left_on = ["x_align","y_align"], 
                 right_on = ["Easting","Northing"], how = "left")

# clean up alignment_stationed_df
try:
    alignment_stationed_df = (
        alignment_stationed_df.drop(columns =["Point", "Type", "Northing", "Easting"]) )
except:
    pass

#alignment_stationed_df.head()
alignment_stationed_df

x_align       y_align  id_point  distance_stat  distance_stat_sum  \
0   634478.260000  6.038563e+06         0       49.38982       15000.000000   
1   634428.888043  6.038565e+06         1       49.38982       15049.389820   
2   634379.516087  6.038566e+06         2       49.38982       15098.779641   
3   634330.144130  6.038567e+06         3       49.38982       15148.169461   
4   634280.772174  6.038569e+06         4       49.38982       15197.559282   
5   634231.400217  6.038570e+06         5       49.38982       15246.949102   
6   634182.028261  6.038571e+06         6       49.38982       15296.338923   
7   634132.656304  6.038573e+06         7       49.38982       15345.728743   
8   634083.284348  6.038574e+06         8       49.38982       15395.118564   
9   634033.912391  6.038575e+06         9       49.38982       15444.508384   
10  633984.540435  6.038577e+06        10       49.38982       15493.898205   
11  633935.168478  6.038578e+06        11       49.38982       15543.288025   
12  633885.796522  6.038579e+06        12       49.38982       15592.677846   
13  633836.424565  6.038581e+06        13       49.38982       15642.067666   
14  633787.052609  6.038582e+06        14       49.38982       15691.457487   
15  633737.680652  6.038583e+06        15       49.38982       15740.847307   
16  633688.308696  6.038585e+06        16       49.38982       15790.237128   
17  633638.936739  6.038586e+06        17       49.38982       15839.626948   
18  633589.564783  6.038587e+06        18       49.38982       15889.016769   
19  633540.192826  6.038589e+06        19       49.38982       15938.406589   
20  633490.820870  6.038590e+06        20       49.38982       15987.796410   
21  633441.448913  6.038591e+06        21       49.38982       16037.186230   
22  633392.076957  6.038593e+06        22       49.38982       16086.576051   
23  633342.705000  6.038594e+06        23       49.38982       16135.965871   
24  633293.333043  6.038595e+06        24       49.38982       16185.355692   
25  633243.961087  6.038597e+06        25       49.38982       16234.745512   
26  633194.589130  6.038598e+06        26       49.38982       16284.135333   
27  633145.217174  6.038599e+06        27       49.38982       16333.525153   
28  633095.845217  6.038601e+06        28       49.38982       16382.914974   
29  633046.473261  6.038602e+06        29       49.38982       16432.304794   
30  632997.101304  6.038603e+06        30       49.38982       16481.694615   
31  632947.729348  6.038605e+06        31       49.38982       16531.084435   
32  632898.357391  6.038606e+06        32       49.38982       16580.474256   
33  632848.985435  6.038607e+06        33       49.38982       16629.864076   
34  632799.613478  6.038609e+06        34       49.38982       16679.253897   
35  632750.241522  6.038610e+06        35       49.38982       16728.643717   
36  632700.869565  6.038611e+06        36       49.38982       16778.033538   
37  632651.497609  6.038613e+06        37       49.38982       16827.423358   
38  632602.125652  6.038614e+06        38       49.38982       16876.813178   
39  632552.753696  6.038615e+06        39       49.38982       16926.202999   
40  632503.381739  6.038617e+06        40       49.38982       16975.592819   
41  632454.009783  6.038618e+06        41       49.38982       17024.982640   
42  632404.637826  6.038619e+06        42       49.38982       17074.372460   
43  632355.265870  6.038621e+06        43       49.38982       17123.762281   
44  632305.893913  6.038622e+06        44       49.38982       17173.152101   
45  632256.521957  6.038623e+06        45       49.38982       17222.541922   
46  632207.150000  6.038625e+06        46        1.00000       17271.931742   
47  632206.150000  6.038625e+06        47       49.07716       17272.931742   
48  632157.090600  6.038626e+06        48       49.07716       17322.008903   
49  632108.031200  6.038627e+06        49       49.07716    

In [31]:
# get id_points for alignment points in alignment_stationed_df 
#   select points where Elevation of point not NaN
id_points_align =  (
    alignment_stationed_df.loc[(alignment_stationed_df.Elevation.isin(alignment_df["Elevation"])), "id_point"] )
id_points_align= id_points_align.tolist()
id_points_align                                                                         

[0, 46, 47, 97]

In [32]:
len(id_points_align)

4

In [33]:
# prepare intermediated data in alignment_stationed_df required to interpolate alignment elevations

# fill in "Elevation" and "distance_intermed_align" for points in alignment_stationed_df 
#   where points of alignment_points_df != alignment_df

# why is this needed??  (why is Elevation filled in ??)                                                                              ToDo: JK
for n in range(0, len(id_points_align) -1): 
    alignment_stationed_df.loc[(alignment_stationed_df.id_point.isin(range(id_points_align[n] +1, 
                                id_points_align[n +1]))), "Elevation"] = ( 
                                                                    alignment_df["Elevation"][n] )

for n in range(0, len(id_points_align) -1): 
    alignment_stationed_df.loc[(alignment_stationed_df.id_point.isin(range(id_points_align[n] +1, 
                                id_points_align[n +1]))), "distance_intermed_align"] = ( 
                                                        alignment_df["distance_intermed_align"][n] )

# add "distance_intermed_stat" to alignment_stationed_df 
alignment_stationed_df["distance_intermed_stat"] = np.nan

for n in range(0, 1):
    alignment_stationed_df.loc[(alignment_stationed_df.id_point.isin(range(id_points_align[n], 
                                id_points_align[n +1] +1))), "distance_intermed_stat"] =  ( 
                                    alignment_stationed_df["distance_stat_sum"] -start_station )  ####
### for n in range(1, len(id_points_align) -1): 
###     alignment_stationed_df.loc[(alignment_stationed_df.id_point.isin(range(id_points_align[n], 
###                                 id_points_align[n +1]))), "distance_intermed_stat"] = ( 
###                                                     alignment_stationed_df["distance_stat_sum"] - 
###                                                     alignment_df["distance_intermed_align"][n -1] )
for n in range(1, len(id_points_align) -1):
      alignment_stationed_df.loc[(alignment_stationed_df.id_point.isin(range(id_points_align[n] +1, 
                                  id_points_align[n +1] +1))), "distance_intermed_stat"] = ( 
                                             alignment_stationed_df["distance_stat_sum"] - 
                                             alignment_stationed_df["distance_stat_sum"][id_points_align[n]] )
    
#alignment_stationed_df.head()
#alignment_stationed_df

In [34]:
alignment_stationed_df

x_align       y_align  id_point  distance_stat  distance_stat_sum  \
0   634478.260000  6.038563e+06         0       49.38982       15000.000000   
1   634428.888043  6.038565e+06         1       49.38982       15049.389820   
2   634379.516087  6.038566e+06         2       49.38982       15098.779641   
3   634330.144130  6.038567e+06         3       49.38982       15148.169461   
4   634280.772174  6.038569e+06         4       49.38982       15197.559282   
5   634231.400217  6.038570e+06         5       49.38982       15246.949102   
6   634182.028261  6.038571e+06         6       49.38982       15296.338923   
7   634132.656304  6.038573e+06         7       49.38982       15345.728743   
8   634083.284348  6.038574e+06         8       49.38982       15395.118564   
9   634033.912391  6.038575e+06         9       49.38982       15444.508384   
10  633984.540435  6.038577e+06        10       49.38982       15493.898205   
11  633935.168478  6.038578e+06        11       49.38982       15543.288025   
12  633885.796522  6.038579e+06        12       49.38982       15592.677846   
13  633836.424565  6.038581e+06        13       49.38982       15642.067666   
14  633787.052609  6.038582e+06        14       49.38982       15691.457487   
15  633737.680652  6.038583e+06        15       49.38982       15740.847307   
16  633688.308696  6.038585e+06        16       49.38982       15790.237128   
17  633638.936739  6.038586e+06        17       49.38982       15839.626948   
18  633589.564783  6.038587e+06        18       49.38982       15889.016769   
19  633540.192826  6.038589e+06        19       49.38982       15938.406589   
20  633490.820870  6.038590e+06        20       49.38982       15987.796410   
21  633441.448913  6.038591e+06        21       49.38982       16037.186230   
22  633392.076957  6.038593e+06        22       49.38982       16086.576051   
23  633342.705000  6.038594e+06        23       49.38982       16135.965871   
24  633293.333043  6.038595e+06        24       49.38982       16185.355692   
25  633243.961087  6.038597e+06        25       49.38982       16234.745512   
26  633194.589130  6.038598e+06        26       49.38982       16284.135333   
27  633145.217174  6.038599e+06        27       49.38982       16333.525153   
28  633095.845217  6.038601e+06        28       49.38982       16382.914974   
29  633046.473261  6.038602e+06        29       49.38982       16432.304794   
30  632997.101304  6.038603e+06        30       49.38982       16481.694615   
31  632947.729348  6.038605e+06        31       49.38982       16531.084435   
32  632898.357391  6.038606e+06        32       49.38982       16580.474256   
33  632848.985435  6.038607e+06        33       49.38982       16629.864076   
34  632799.613478  6.038609e+06        34       49.38982       16679.253897   
35  632750.241522  6.038610e+06        35       49.38982       16728.643717   
36  632700.869565  6.038611e+06        36       49.38982       16778.033538   
37  632651.497609  6.038613e+06        37       49.38982       16827.423358   
38  632602.125652  6.038614e+06        38       49.38982       16876.813178   
39  632552.753696  6.038615e+06        39       49.38982       16926.202999   
40  632503.381739  6.038617e+06        40       49.38982       16975.592819   
41  632454.009783  6.038618e+06        41       49.38982       17024.982640   
42  632404.637826  6.038619e+06        42       49.38982       17074.372460   
43  632355.265870  6.038621e+06        43       49.38982       17123.762281   
44  632305.893913  6.038622e+06        44       49.38982       17173.152101   
45  632256.521957  6.038623e+06        45       49.38982       17222.541922   
46  632207.150000  6.038625e+06        46        1.00000       17271.931742   
47  632206.150000  6.038625e+06        47       49.07716       17272.931742   
48  632157.090600  6.038626e+06        48       49.07716       17322.008903   
49  632108.031200  6.038627e+06        49       49.07716    

In [35]:
# interpolate alignment elevation ("z_align") at all station points and write to alignment_stationed_df

# add variable "z_align" to alignment_stationed_df
alignment_stationed_df["z_align"] = np.nan

for i in range(0, len(alignment_stationed_df)):
    print('i: ',i)
    # alignment points
    if i in id_points_align:
        alignment_stationed_df.iloc[i, alignment_stationed_df.columns.get_loc("z_align")] = ( 
                                                        alignment_stationed_df.iloc[i]["Elevation"] )
    # stationed points
    else:
        id_points_align_plus_point_n = id_points_align
        id_points_align_plus_point_n.append(i)
        id_points_align_plus_point_n.sort()
        m = id_points_align_plus_point_n.index(i) +1  #index of point n +1 (next alignment point)
        n = id_points_align_plus_point_n[m]  #id_point of next alignment point  
        o = id_points_align_plus_point_n.index(i) -1  #index of point n -1 (previous alignment point)
        p = id_points_align_plus_point_n[o]  #id_point of previous alignment point
        print('m,n,o,p: ',m,n,o,p)
        print('p-EL,n-EL,i_dist_inter_al,i-1_dist_inter_sta: ', 
                            alignment_stationed_df.iloc[p]["Elevation"],
                            alignment_stationed_df.iloc[n]["Elevation"], 
                            alignment_stationed_df.iloc[i]["distance_intermed_align"],
                            alignment_stationed_df.iloc[i-1]["distance_intermed_stat"])
                                                           
        alignment_stationed_df.iloc[i, alignment_stationed_df.columns.get_loc("z_align")] = ( 
                         alignment_stationed_df.iloc[p]["Elevation"] 
                         +(alignment_stationed_df.iloc[n]["Elevation"] 
                         -alignment_stationed_df.iloc[p]["Elevation"]) 
                             /alignment_stationed_df.iloc[i]["distance_intermed_align"]
                             *alignment_stationed_df.iloc[i]["distance_intermed_stat"] )
                             ####*alignment_stationed_df.iloc[i-1]["distance_intermed_stat"] )
        
        id_points_align_plus_point_n.remove(i)  #needed ??                                           #ToDo JK

alignment_stationed_df = alignment_stationed_df.drop(columns = ["distance_intermed_align"])
alignment_stationed_df = alignment_stationed_df.drop(columns = ["distance_intermed_stat"])
alignment_stationed_df = alignment_stationed_df.drop(columns = ["Elevation"])

#alignment_stationed_df.head()
#alignment_stationed_df

('i: ', 0)
('i: ', 1)
('m,n,o,p: ', 2, 46, 0, 0)
('p-EL,n-EL,i_dist_inter_al,i-1_dist_inter_sta: ', 1111.11, 1105.17, 2271.93174239454, 0.0)
('i: ', 2)
('m,n,o,p: ', 2, 46, 0, 0)
('p-EL,n-EL,i_dist_inter_al,i-1_dist_inter_sta: ', 1111.11, 1105.17, 2271.93174239454, 49.389820486865574)
('i: ', 3)
('m,n,o,p: ', 2, 46, 0, 0)
('p-EL,n-EL,i_dist_inter_al,i-1_dist_inter_sta: ', 1111.11, 1105.17, 2271.93174239454, 98.77964097372933)
('i: ', 4)
('m,n,o,p: ', 2, 46, 0, 0)
('p-EL,n-EL,i_dist_inter_al,i-1_dist_inter_sta: ', 1111.11, 1105.17, 2271.93174239454, 148.16946146045302)
('i: ', 5)
('m,n,o,p: ', 2, 46, 0, 0)
('p-EL,n-EL,i_dist_inter_al,i-1_dist_inter_sta: ', 1111.11, 1105.17, 2271.93174239454, 197.5592819473186)
('i: ', 6)
('m,n,o,p: ', 2, 46, 0, 0)
('p-EL,n-EL,i_dist_inter_al,i-1_dist_inter_sta: ', 1111.11, 1105.17, 2271.93174239454, 246.94910243418417)
('i: ', 7)
('m,n,o,p: ', 2, 46, 0, 0)
('p-EL,n-EL,i_dist_inter_al,i-1_dist_inter_sta: ', 1111.11, 1105.17, 2271.93174239454, 296.3389229

('m,n,o,p: ', 4, 97, 2, 47)
('p-EL,n-EL,i_dist_inter_al,i-1_dist_inter_sta: ', 690.485, 445.0, 2453.858011580938, 1226.92900579048)
('i: ', 74)
('m,n,o,p: ', 4, 97, 2, 47)
('p-EL,n-EL,i_dist_inter_al,i-1_dist_inter_sta: ', 690.485, 445.0, 2453.858011580938, 1276.0061660221254)
('i: ', 75)
('m,n,o,p: ', 4, 97, 2, 47)
('p-EL,n-EL,i_dist_inter_al,i-1_dist_inter_sta: ', 690.485, 445.0, 2453.858011580938, 1325.0833262537708)
('i: ', 76)
('m,n,o,p: ', 4, 97, 2, 47)
('p-EL,n-EL,i_dist_inter_al,i-1_dist_inter_sta: ', 690.485, 445.0, 2453.858011580938, 1374.1604864852998)
('i: ', 77)
('m,n,o,p: ', 4, 97, 2, 47)
('p-EL,n-EL,i_dist_inter_al,i-1_dist_inter_sta: ', 690.485, 445.0, 2453.858011580938, 1423.2376467169452)
('i: ', 78)
('m,n,o,p: ', 4, 97, 2, 47)
('p-EL,n-EL,i_dist_inter_al,i-1_dist_inter_sta: ', 690.485, 445.0, 2453.858011580938, 1472.3148069485906)
('i: ', 79)
('m,n,o,p: ', 4, 97, 2, 47)
('p-EL,n-EL,i_dist_inter_al,i-1_dist_inter_sta: ', 690.485, 445.0, 2453.858011580938, 1521.3919671

In [36]:
alignment_stationed_df

x_align       y_align  id_point  distance_stat  distance_stat_sum  \
0   634478.260000  6.038563e+06         0       49.38982       15000.000000   
1   634428.888043  6.038565e+06         1       49.38982       15049.389820   
2   634379.516087  6.038566e+06         2       49.38982       15098.779641   
3   634330.144130  6.038567e+06         3       49.38982       15148.169461   
4   634280.772174  6.038569e+06         4       49.38982       15197.559282   
5   634231.400217  6.038570e+06         5       49.38982       15246.949102   
6   634182.028261  6.038571e+06         6       49.38982       15296.338923   
7   634132.656304  6.038573e+06         7       49.38982       15345.728743   
8   634083.284348  6.038574e+06         8       49.38982       15395.118564   
9   634033.912391  6.038575e+06         9       49.38982       15444.508384   
10  633984.540435  6.038577e+06        10       49.38982       15493.898205   
11  633935.168478  6.038578e+06        11       49.38982       15543.288025   
12  633885.796522  6.038579e+06        12       49.38982       15592.677846   
13  633836.424565  6.038581e+06        13       49.38982       15642.067666   
14  633787.052609  6.038582e+06        14       49.38982       15691.457487   
15  633737.680652  6.038583e+06        15       49.38982       15740.847307   
16  633688.308696  6.038585e+06        16       49.38982       15790.237128   
17  633638.936739  6.038586e+06        17       49.38982       15839.626948   
18  633589.564783  6.038587e+06        18       49.38982       15889.016769   
19  633540.192826  6.038589e+06        19       49.38982       15938.406589   
20  633490.820870  6.038590e+06        20       49.38982       15987.796410   
21  633441.448913  6.038591e+06        21       49.38982       16037.186230   
22  633392.076957  6.038593e+06        22       49.38982       16086.576051   
23  633342.705000  6.038594e+06        23       49.38982       16135.965871   
24  633293.333043  6.038595e+06        24       49.38982       16185.355692   
25  633243.961087  6.038597e+06        25       49.38982       16234.745512   
26  633194.589130  6.038598e+06        26       49.38982       16284.135333   
27  633145.217174  6.038599e+06        27       49.38982       16333.525153   
28  633095.845217  6.038601e+06        28       49.38982       16382.914974   
29  633046.473261  6.038602e+06        29       49.38982       16432.304794   
30  632997.101304  6.038603e+06        30       49.38982       16481.694615   
31  632947.729348  6.038605e+06        31       49.38982       16531.084435   
32  632898.357391  6.038606e+06        32       49.38982       16580.474256   
33  632848.985435  6.038607e+06        33       49.38982       16629.864076   
34  632799.613478  6.038609e+06        34       49.38982       16679.253897   
35  632750.241522  6.038610e+06        35       49.38982       16728.643717   
36  632700.869565  6.038611e+06        36       49.38982       16778.033538   
37  632651.497609  6.038613e+06        37       49.38982       16827.423358   
38  632602.125652  6.038614e+06        38       49.38982       16876.813178   
39  632552.753696  6.038615e+06        39       49.38982       16926.202999   
40  632503.381739  6.038617e+06        40       49.38982       16975.592819   
41  632454.009783  6.038618e+06        41       49.38982       17024.982640   
42  632404.637826  6.038619e+06        42       49.38982       17074.372460   
43  632355.265870  6.038621e+06        43       49.38982       17123.762281   
44  632305.893913  6.038622e+06        44       49.38982       17173.152101   
45  632256.521957  6.038623e+06        45       49.38982       17222.541922   
46  632207.150000  6.038625e+06        46        1.00000       17271.931742   
47  632206.150000  6.038625e+06        47       49.07716       17272.931742   
48  632157.090600  6.038626e+06        48       49.07716       17322.008903   
49  632108.031200  6.038627e+06        49       49.07716    

In [37]:
# add required field "z_dtm_align" to alignment_stationed_df 

# list of shapely geometry points                                                #ToDo JK: make df -> shp function           
alignment_stationed_geometry = ( 
    [sp.geometry.Point(row['x_align'], row['y_align']) for key, row in alignment_stationed_df.iterrows()] )
# create alignment_stationed_geometry_df
alignment_stationed_geometry_df = ( 
    gpd.GeoDataFrame(alignment_stationed_df, geometry=alignment_stationed_geometry, crs = crs) )
# write df to Alignment_stationed_shp (overwrite file)
alignment_stationed_geometry_df.to_file(Alignment_stationed_shp, driver='ESRI Shapefile') 

# get DTM values for alignment_points                                     #ToDo JK: make into what.points function
#   write to Alignment_dtm_csv
processing.runalg("grass7:r.what.points",DTM,Alignment_stationed_shp, "NA",",", 500,
                  True,False,False,False,False,grass_region,-1,0.0001,Alignment_dtm_csv)

# create alignment_dtm_df (dataframe) from Alignment_dtm_csv 
alignment_dtm_df = pd.read_csv(Alignment_dtm_csv)

# rename col=tmp... to "z_dtm_align"
alignment_dtm_df_col_tmp = [col for col in alignment_dtm_df.columns if 'tmp' in col]
if len(alignment_dtm_df_col_tmp) != 1:
    print "Extraction of DTM col=tmp did not work properly for alignment. Please check"
    exit()
alignment_dtm_df = alignment_dtm_df.rename(
    columns= {alignment_dtm_df_col_tmp[0]: "z_dtm_align"})

# write alignment_dtm_df["z_dtm_align"] to alignment_stationed_df["z_dtm_align"]
alignment_stationed_df["z_dtm_align"] = alignment_dtm_df["z_dtm_align"]

alignment_stationed_df = alignment_stationed_df.drop(columns = ["geometry"])

#alignment_stationed_df.head()
alignment_stationed_df

x_align       y_align  id_point  distance_stat  distance_stat_sum  \
0   634478.260000  6.038563e+06         0       49.38982       15000.000000   
1   634428.888043  6.038565e+06         1       49.38982       15049.389820   
2   634379.516087  6.038566e+06         2       49.38982       15098.779641   
3   634330.144130  6.038567e+06         3       49.38982       15148.169461   
4   634280.772174  6.038569e+06         4       49.38982       15197.559282   
5   634231.400217  6.038570e+06         5       49.38982       15246.949102   
6   634182.028261  6.038571e+06         6       49.38982       15296.338923   
7   634132.656304  6.038573e+06         7       49.38982       15345.728743   
8   634083.284348  6.038574e+06         8       49.38982       15395.118564   
9   634033.912391  6.038575e+06         9       49.38982       15444.508384   
10  633984.540435  6.038577e+06        10       49.38982       15493.898205   
11  633935.168478  6.038578e+06        11       49.38982       15543.288025   
12  633885.796522  6.038579e+06        12       49.38982       15592.677846   
13  633836.424565  6.038581e+06        13       49.38982       15642.067666   
14  633787.052609  6.038582e+06        14       49.38982       15691.457487   
15  633737.680652  6.038583e+06        15       49.38982       15740.847307   
16  633688.308696  6.038585e+06        16       49.38982       15790.237128   
17  633638.936739  6.038586e+06        17       49.38982       15839.626948   
18  633589.564783  6.038587e+06        18       49.38982       15889.016769   
19  633540.192826  6.038589e+06        19       49.38982       15938.406589   
20  633490.820870  6.038590e+06        20       49.38982       15987.796410   
21  633441.448913  6.038591e+06        21       49.38982       16037.186230   
22  633392.076957  6.038593e+06        22       49.38982       16086.576051   
23  633342.705000  6.038594e+06        23       49.38982       16135.965871   
24  633293.333043  6.038595e+06        24       49.38982       16185.355692   
25  633243.961087  6.038597e+06        25       49.38982       16234.745512   
26  633194.589130  6.038598e+06        26       49.38982       16284.135333   
27  633145.217174  6.038599e+06        27       49.38982       16333.525153   
28  633095.845217  6.038601e+06        28       49.38982       16382.914974   
29  633046.473261  6.038602e+06        29       49.38982       16432.304794   
30  632997.101304  6.038603e+06        30       49.38982       16481.694615   
31  632947.729348  6.038605e+06        31       49.38982       16531.084435   
32  632898.357391  6.038606e+06        32       49.38982       16580.474256   
33  632848.985435  6.038607e+06        33       49.38982       16629.864076   
34  632799.613478  6.038609e+06        34       49.38982       16679.253897   
35  632750.241522  6.038610e+06        35       49.38982       16728.643717   
36  632700.869565  6.038611e+06        36       49.38982       16778.033538   
37  632651.497609  6.038613e+06        37       49.38982       16827.423358   
38  632602.125652  6.038614e+06        38       49.38982       16876.813178   
39  632552.753696  6.038615e+06        39       49.38982       16926.202999   
40  632503.381739  6.038617e+06        40       49.38982       16975.592819   
41  632454.009783  6.038618e+06        41       49.38982       17024.982640   
42  632404.637826  6.038619e+06        42       49.38982       17074.372460   
43  632355.265870  6.038621e+06        43       49.38982       17123.762281   
44  632305.893913  6.038622e+06        44       49.38982       17173.152101   
45  632256.521957  6.038623e+06        45       49.38982       17222.541922   
46  632207.150000  6.038625e+06        46        1.00000       17271.931742   
47  632206.150000  6.038625e+06        47       49.07716       17272.931742   
48  632157.090600  6.038626e+06        48       49.07716       17322.008903   
49  632108.031200  6.038627e+06        49       49.07716    

In [38]:
# Add require field "h" to alignment_stationed_df = overburden depth above station point 
alignment_stationed_df["h"] = alignment_stationed_df["z_dtm_align"] - alignment_stationed_df["z_align"] 

#alignment_stationed_df.head()
alignment_stationed_df

x_align       y_align  id_point  distance_stat  distance_stat_sum  \
0   634478.260000  6.038563e+06         0       49.38982       15000.000000   
1   634428.888043  6.038565e+06         1       49.38982       15049.389820   
2   634379.516087  6.038566e+06         2       49.38982       15098.779641   
3   634330.144130  6.038567e+06         3       49.38982       15148.169461   
4   634280.772174  6.038569e+06         4       49.38982       15197.559282   
5   634231.400217  6.038570e+06         5       49.38982       15246.949102   
6   634182.028261  6.038571e+06         6       49.38982       15296.338923   
7   634132.656304  6.038573e+06         7       49.38982       15345.728743   
8   634083.284348  6.038574e+06         8       49.38982       15395.118564   
9   634033.912391  6.038575e+06         9       49.38982       15444.508384   
10  633984.540435  6.038577e+06        10       49.38982       15493.898205   
11  633935.168478  6.038578e+06        11       49.38982       15543.288025   
12  633885.796522  6.038579e+06        12       49.38982       15592.677846   
13  633836.424565  6.038581e+06        13       49.38982       15642.067666   
14  633787.052609  6.038582e+06        14       49.38982       15691.457487   
15  633737.680652  6.038583e+06        15       49.38982       15740.847307   
16  633688.308696  6.038585e+06        16       49.38982       15790.237128   
17  633638.936739  6.038586e+06        17       49.38982       15839.626948   
18  633589.564783  6.038587e+06        18       49.38982       15889.016769   
19  633540.192826  6.038589e+06        19       49.38982       15938.406589   
20  633490.820870  6.038590e+06        20       49.38982       15987.796410   
21  633441.448913  6.038591e+06        21       49.38982       16037.186230   
22  633392.076957  6.038593e+06        22       49.38982       16086.576051   
23  633342.705000  6.038594e+06        23       49.38982       16135.965871   
24  633293.333043  6.038595e+06        24       49.38982       16185.355692   
25  633243.961087  6.038597e+06        25       49.38982       16234.745512   
26  633194.589130  6.038598e+06        26       49.38982       16284.135333   
27  633145.217174  6.038599e+06        27       49.38982       16333.525153   
28  633095.845217  6.038601e+06        28       49.38982       16382.914974   
29  633046.473261  6.038602e+06        29       49.38982       16432.304794   
30  632997.101304  6.038603e+06        30       49.38982       16481.694615   
31  632947.729348  6.038605e+06        31       49.38982       16531.084435   
32  632898.357391  6.038606e+06        32       49.38982       16580.474256   
33  632848.985435  6.038607e+06        33       49.38982       16629.864076   
34  632799.613478  6.038609e+06        34       49.38982       16679.253897   
35  632750.241522  6.038610e+06        35       49.38982       16728.643717   
36  632700.869565  6.038611e+06        36       49.38982       16778.033538   
37  632651.497609  6.038613e+06        37       49.38982       16827.423358   
38  632602.125652  6.038614e+06        38       49.38982       16876.813178   
39  632552.753696  6.038615e+06        39       49.38982       16926.202999   
40  632503.381739  6.038617e+06        40       49.38982       16975.592819   
41  632454.009783  6.038618e+06        41       49.38982       17024.982640   
42  632404.637826  6.038619e+06        42       49.38982       17074.372460   
43  632355.265870  6.038621e+06        43       49.38982       17123.762281   
44  632305.893913  6.038622e+06        44       49.38982       17173.152101   
45  632256.521957  6.038623e+06        45       49.38982       17222.541922   
46  632207.150000  6.038625e+06        46        1.00000       17271.931742   
47  632206.150000  6.038625e+06        47       49.07716       17272.931742   
48  632157.090600  6.038626e+06        48       49.07716       17322.008903   
49  632108.031200  6.038627e+06        49       49.07716    

In [39]:
# define make_buffer to get buffer grid points at all station points along alignment
def make_buffer(point, overburden, c, res):
    h = overburden
    if h < 0.0:
        print "Overburden is negative. Please check"
        exit()
    intvls_r = max(int(h*c / res), 1)  #number of intervals along the buffer radius, close enough
    res_r = h*c / intvls_r  #effective resolution along the radius
    buffer = np.array(point)  #initialize buffer, first item is exactly at station point

    # calculate local coordinates for grid along a ring and add to point coor
    for i in range(intvls_r):
        r = c*h - i*res_r
        perim = 2 * r * pi 
        intvls_c = max(int(perim/res), 1)  #number of intervals along a ring, close enough
        item = np.array([0.0, 0.0])  #initialize       
        for j in range(intvls_c):
            item[0] = (sin((2*pi) / intvls_c *(j+1)) *r) + point[0]
            item[1] = (cos((2*pi) / intvls_c *(j+1)) *r) + point[1]
            buffer = np.vstack((buffer, item))  #vstack works with arrays of diff nr of items, append does not        

    return buffer

In [40]:
# create csv file with all buffer points     #ToDo KLK: make check plot of alignment, station points, buffer_all

# point = alignment_stationed_xy
# create alignment_stationed_xy from alignment_stationed_df with x,y of all station points
alignment_stationed_xy = alignment_stationed_df.as_matrix(columns=['x_align','y_align'])
# overburden = alignment_stationed_h
alignment_stationed_h = alignment_stationed_df.as_matrix(columns=['h'])

# initialize buffer_df, buffer_all_df, buffer_all
buffer_all = {}
buffer_df = pd.DataFrame(columns=["id_point", "x_align", "y_align", "z_align", "h" ,"x_buffer", "y_buffer"])
buffer_all_df = pd.DataFrame(columns=["id_point", "x_align", "y_align", "z_align", "h","x_buffer", "y_buffer"])

for n in range(0, len(alignment_stationed_df)):
    ####print('n: ',n)
    buffer_point = make_buffer(point=alignment_stationed_xy[n], overburden=alignment_stationed_h[n], c=c, res=res)
    buffer_all[n] = buffer_df.copy(deep=False)  #copy of initialized buffer_df
    #print("n: ", n)
    #print(buffer_all)
    buffer_all[n]["id_point"] = [n] * len(buffer_point)  #list with len(buffer_point) number of n values) 
    ####buffer_all[n]["stat_sum"] = (  #make stat_sum correct for point n
    ####    [alignment_stationed_df.iloc[n-1, alignment_stationed_df.columns.get_loc("distance_stat_sum")]] * len(buffer_point) ) 
    buffer_all[n]["stat_sum"] = (  #make stat_sum correct for point n
        [alignment_stationed_df.iloc[n, alignment_stationed_df.columns.get_loc("distance_stat_sum")]] * len(buffer_point) ) 
    ####buffer_all[n]["dist_stat"] = (  #make stat_sum correct for point n
    ####    [alignment_stationed_df.iloc[n-1, alignment_stationed_df.columns.get_loc("distance_stat")]] * len(buffer_point) ) 
    buffer_all[n]["dist_stat"] = (  #make stat_sum correct for point n
        [alignment_stationed_df.iloc[n, alignment_stationed_df.columns.get_loc("distance_stat")]] * len(buffer_point) ) 
    buffer_all[n]["x_align"] = ( 
        [alignment_stationed_df.iloc[n, alignment_stationed_df.columns.get_loc("x_align")]] * len(buffer_point) )      
    buffer_all[n]["y_align"] = ( 
        [alignment_stationed_df.iloc[n, alignment_stationed_df.columns.get_loc("y_align")]] * len(buffer_point) )      
    buffer_all[n]["z_align"] = ( 
        [alignment_stationed_df.iloc[n, alignment_stationed_df.columns.get_loc("z_align")]] * len(buffer_point) )           
    buffer_all[n]["h"] = ( 
        [alignment_stationed_df.iloc[n, alignment_stationed_df.columns.get_loc("h")]] * len(buffer_point) )           
    buffer_all[n]["x_buffer"] = buffer_point[0:,0]
    buffer_all[n]["y_buffer"] = buffer_point[0:,1]
    buffer_all_df = pd.concat([buffer_all_df, buffer_all[n]])
    #print(buffer_all_df)

# add variable "id_buffer_point" to buffer_all_df
buffer_all_df = buffer_all_df.reset_index(drop=True)
buffer_all_df["id_buffer_point"] = buffer_all_df.index    

# save buffer_all_df to csv
buffer_all_df.to_csv(Buffer_all_csv, sep=",", na_rep="NaN")

buffer_all_df.head()

dist_stat       h id_point  stat_sum    x_align       x_buffer     y_align  \
0   49.38982  358.89        0   15000.0  634478.26  634478.260000  6038563.42   
1   49.38982  358.89        0   15000.0  634478.26  634503.233917  6038563.42   
2   49.38982  358.89        0   15000.0  634478.26  634527.721745  6038563.42   
3   49.38982  358.89        0   15000.0  634478.26  634551.246857  6038563.42   
4   49.38982  358.89        0   15000.0  634478.26  634573.351362  6038563.42   

       y_buffer  z_align  id_buffer_point  
0  6.038563e+06  1111.11                0  
1  6.038741e+06  1111.11                1  
2  6.038736e+06  1111.11                2  
3  6.038727e+06  1111.11                3  
4  6.038716e+06  1111.11                4

In [41]:
# add required field "z_dtm_buffer" and calcualted "dist" to buffer_all_df 
# add required field "slope" to buffer_all_df 

# buffer_all_df to Buffer_all_shp                                   #ToDo JK: reuse df -> shp function from above
# list of shapely geometry points
buffer_all_geometry = ( 
    [sp.geometry.Point(row['x_buffer'], row['y_buffer']) for key, row in buffer_all_df.iterrows()] )
# create buffer_all_geometry_df
buffer_all_geometry_df = gpd.GeoDataFrame(buffer_all_df, geometry=buffer_all_geometry, crs = crs)
# write df to Buffer_all_shp
buffer_all_geometry_df.to_file(Buffer_all_shp, driver='ESRI Shapefile') 
#print(buffer_all_geometry_df.head())

# get DTM values for Buffer_all_shp                             #ToDo JK: reuse what.points function from above
#   write to Buffer_dtm_csv
processing.runalg("grass7:r.what.points",DTM,Buffer_all_shp, "NA",",", 500,True,False,False,False,False,
                  grass_region,-1,0.0001,Buffer_dtm_csv)

# create buffer_dtm_df (dataframe) from Buffer_dtm_csv
buffer_dtm_df = pd.read_csv(Buffer_dtm_csv)

# rename col=tmp... to "z_dtm_buffer"
buffer_dtm_df_col_tmp = [col for col in buffer_dtm_df.columns if 'tmp' in col]
if len(buffer_dtm_df_col_tmp) != 1:
    print "Extraction of DTM col=tmp did not work properly for buffer. Please check"
    exit()
buffer_dtm_df = buffer_dtm_df.rename(
    columns= {buffer_dtm_df_col_tmp[0]: "z_dtm_buffer"})
#print(buffer_dtm_df.head())

# write buffer_dtm_df["z_dtm"] to buffer_all_df["z_dtm"]
buffer_all_df["z_dtm_buffer"] = buffer_dtm_df["z_dtm_buffer"]
#print(buffer_all_df.head())


# get slope values for Buffer_all_shp
#   write to Buffer_slope_csv
processing.runalg("grass7:r.what.points",DTM_slope,Buffer_all_shp, "NA",",", 500,True,False,False,False,False,
                  grass_region,-1,0.0001,Buffer_slope_csv)

# create buffer_dtm_df (dataframe) from Buffer_dtm_csv
buffer_slope_df = pd.read_csv(Buffer_slope_csv)

# rename col=tmp... to "z_dtm_buffer"
buffer_slope_df_col_tmp = [col for col in buffer_slope_df.columns if 'tmp' in col]
if len(buffer_slope_df_col_tmp) != 1:
    print "Extraction of Slope col=tmp did not work properly for buffer. Please check"
    exit()
buffer_slope_df = buffer_slope_df.rename(
    columns= {buffer_slope_df_col_tmp[0]: "slope"})
#print(buffer_slope_df.head())

# write buffer_dtm_df["z_dtm"] to buffer_all_df["z_dtm"]
buffer_all_df["slope"] = buffer_slope_df["slope"]


# calculate "dist" between each buffer point and associated alignment point 
buffer_all_df["dist"] = (((buffer_all_df["x_align"] - buffer_all_df["x_buffer"])**2 + 
                         (buffer_all_df["y_align"] - buffer_all_df["y_buffer"]) **2) +
                         (buffer_all_df["z_dtm_buffer"] - buffer_all_df["z_align"]) **2) **(0.5)

# clean up
buffer_all_df = buffer_all_df.drop(columns =["geometry"])
buffer_all_df.head()

dist_stat       h id_point  stat_sum    x_align       x_buffer     y_align  \
0   49.38982  358.89        0   15000.0  634478.26  634478.260000  6038563.42   
1   49.38982  358.89        0   15000.0  634478.26  634503.233917  6038563.42   
2   49.38982  358.89        0   15000.0  634478.26  634527.721745  6038563.42   
3   49.38982  358.89        0   15000.0  634478.26  634551.246857  6038563.42   
4   49.38982  358.89        0   15000.0  634478.26  634573.351362  6038563.42   

       y_buffer  z_align  id_buffer_point  z_dtm_buffer     slope        dist  
0  6.038563e+06  1111.11                0   1470.000000  9.846343  358.890000  
1  6.038741e+06  1111.11                1   1481.715854  1.294057  411.763533  
2  6.038736e+06  1111.11                2   1481.715854  1.294057  411.763533  
3  6.038727e+06  1111.11                3   1481.171500  1.280683  411.273658  
4  6.038716e+06  1111.11                4   1480.790139  2.061807  410.930546

In [42]:
#buffer_all_df
buffer_all_df.tail(100)

dist_stat      h id_point      stat_sum    x_align       x_buffer  \
30515        NaN  615.0       97  19726.789754  629753.18  629640.062449   
30516        NaN  615.0       97  19726.789754  629753.18  629658.744795   
30517        NaN  615.0       97  19726.789754  629753.18  629680.003088   
30518        NaN  615.0       97  19726.789754  629753.18  629703.257457   
30519        NaN  615.0       97  19726.789754  629753.18  629727.873582   
30520        NaN  615.0       97  19726.789754  629753.18  629753.180000   
30521        NaN  615.0       97  19726.789754  629753.18  629778.175948   
30522        NaN  615.0       97  19726.789754  629753.18  629802.211315   
30523        NaN  615.0       97  19726.789754  629753.18  629824.362436   
30524        NaN  615.0       97  19726.789754  629753.18  629843.778056   
30525        NaN  615.0       97  19726.789754  629753.18  629859.712044   
30526        NaN  615.0       97  19726.789754  629753.18  629871.552065   
30527        NaN  615.0       97  19726.789754  629753.18  629878.843114   
30528        NaN  615.0       97  19726.789754  629753.18  629881.305000   
30529        NaN  615.0       97  19726.789754  629753.18  629878.843114   
30530        NaN  615.0       97  19726.789754  629753.18  629871.552065   
30531        NaN  615.0       97  19726.789754  629753.18  629859.712044   
30532        NaN  615.0       97  19726.789754  629753.18  629843.778056   
30533        NaN  615.0       97  19726.789754  629753.18  629824.362436   
30534        NaN  615.0       97  19726.789754  629753.18  629802.211315   
30535        NaN  615.0       97  19726.789754  629753.18  629778.175948   
30536        NaN  615.0       97  19726.789754  629753.18  629753.180000   
30537        NaN  615.0       97  19726.789754  629753.18  629728.184052   
30538        NaN  615.0       97  19726.789754  629753.18  629704.148685   
30539        NaN  615.0       97  19726.789754  629753.18  629681.997564   
30540        NaN  615.0       97  19726.789754  629753.18  629662.581944   
30541        NaN  615.0       97  19726.789754  629753.18  629646.647956   
30542        NaN  615.0       97  19726.789754  629753.18  629634.807935   
30543        NaN  615.0       97  19726.789754  629753.18  629627.516886   
30544        NaN  615.0       97  19726.789754  629753.18  629625.055000   
30545        NaN  615.0       97  19726.789754  629753.18  629627.516886   
30546        NaN  615.0       97  19726.789754  629753.18  629634.807935   
30547        NaN  615.0       97  19726.789754  629753.18  629646.647956   
30548        NaN  615.0       97  19726.789754  629753.18  629662.581944   
30549        NaN  615.0       97  19726.789754  629753.18  629681.997564   
30550        NaN  615.0       97  19726.789754  629753.18  629704.148685   
30551        NaN  615.0       97  19726.789754  629753.18  629728.184052   
30552        NaN  615.0       97  19726.789754  629753.18  629753.180000   
30553        NaN  615.0       97  19726.789754  629753.18  629778.670713   
30554        NaN  615.0       97  19726.789754  629753.18  629802.559752   
30555        NaN  615.0       97  19726.789754  629753.18  629823.346078   
30556        NaN  615.0       97  19726.789754  629753.18  629839.723612   
30557        NaN  615.0       97  19726.789754  629753.18  629850.663293   
30558        NaN  615.0       97  19726.789754  629753.18  629855.477740   
30559        NaN  615.0       97  19726.789754  629753.18  629853.864443   
30560        NaN  615.0       97  19726.789754  629753.18  629845.924773   
30561        NaN  615.0       97  19726.789754  629753.18  629832.157607   
30562        NaN  615.0       97  19726.789754  629753.18  629813.427988   
30563        NaN  615.0       97  19726.789754  629753.18  629790.912767   
30564        NaN  615.0       97  19726.789754  629753.18  629766.026656   
30565        NaN  615.0       97  19726.789754  629753.18  629740.333344   
30566        NaN  615.0       97  19726.789754  629753.

In [43]:
# calculate minimum distance to terrain in each buffer ring
                                                #ToDo KLK: make check plot of id_buffer_points with "min_dist"
                                                #ToDo JK: add station field
buffer_all_df["min_dist"] = np.nan

for n in range(0, len(alignment_stationed_df)):
    buffer_all_df_sel = buffer_all_df.loc[(buffer_all_df["id_point"] == n),]
    dist_idxmin=buffer_all_df_sel['dist'].idxmin()
    buffer_all_df.loc[(buffer_all_df["id_buffer_point"] == dist_idxmin), "min_dist"] = "MIN"

buffer_all_df.to_csv(Buffer_all_csv, header=True, index=False)  #no header
#buffer_all_df
buffer_all_df.tail(100)

#buffer_all_df.loc[(buffer_all_df["min_dist"] == "MIN"),]

dist_stat      h id_point      stat_sum    x_align       x_buffer  \
30515        NaN  615.0       97  19726.789754  629753.18  629640.062449   
30516        NaN  615.0       97  19726.789754  629753.18  629658.744795   
30517        NaN  615.0       97  19726.789754  629753.18  629680.003088   
30518        NaN  615.0       97  19726.789754  629753.18  629703.257457   
30519        NaN  615.0       97  19726.789754  629753.18  629727.873582   
30520        NaN  615.0       97  19726.789754  629753.18  629753.180000   
30521        NaN  615.0       97  19726.789754  629753.18  629778.175948   
30522        NaN  615.0       97  19726.789754  629753.18  629802.211315   
30523        NaN  615.0       97  19726.789754  629753.18  629824.362436   
30524        NaN  615.0       97  19726.789754  629753.18  629843.778056   
30525        NaN  615.0       97  19726.789754  629753.18  629859.712044   
30526        NaN  615.0       97  19726.789754  629753.18  629871.552065   
30527        NaN  615.0       97  19726.789754  629753.18  629878.843114   
30528        NaN  615.0       97  19726.789754  629753.18  629881.305000   
30529        NaN  615.0       97  19726.789754  629753.18  629878.843114   
30530        NaN  615.0       97  19726.789754  629753.18  629871.552065   
30531        NaN  615.0       97  19726.789754  629753.18  629859.712044   
30532        NaN  615.0       97  19726.789754  629753.18  629843.778056   
30533        NaN  615.0       97  19726.789754  629753.18  629824.362436   
30534        NaN  615.0       97  19726.789754  629753.18  629802.211315   
30535        NaN  615.0       97  19726.789754  629753.18  629778.175948   
30536        NaN  615.0       97  19726.789754  629753.18  629753.180000   
30537        NaN  615.0       97  19726.789754  629753.18  629728.184052   
30538        NaN  615.0       97  19726.789754  629753.18  629704.148685   
30539        NaN  615.0       97  19726.789754  629753.18  629681.997564   
30540        NaN  615.0       97  19726.789754  629753.18  629662.581944   
30541        NaN  615.0       97  19726.789754  629753.18  629646.647956   
30542        NaN  615.0       97  19726.789754  629753.18  629634.807935   
30543        NaN  615.0       97  19726.789754  629753.18  629627.516886   
30544        NaN  615.0       97  19726.789754  629753.18  629625.055000   
30545        NaN  615.0       97  19726.789754  629753.18  629627.516886   
30546        NaN  615.0       97  19726.789754  629753.18  629634.807935   
30547        NaN  615.0       97  19726.789754  629753.18  629646.647956   
30548        NaN  615.0       97  19726.789754  629753.18  629662.581944   
30549        NaN  615.0       97  19726.789754  629753.18  629681.997564   
30550        NaN  615.0       97  19726.789754  629753.18  629704.148685   
30551        NaN  615.0       97  19726.789754  629753.18  629728.184052   
30552        NaN  615.0       97  19726.789754  629753.18  629753.180000   
30553        NaN  615.0       97  19726.789754  629753.18  629778.670713   
30554        NaN  615.0       97  19726.789754  629753.18  629802.559752   
30555        NaN  615.0       97  19726.789754  629753.18  629823.346078   
30556        NaN  615.0       97  19726.789754  629753.18  629839.723612   
30557        NaN  615.0       97  19726.789754  629753.18  629850.663293   
30558        NaN  615.0       97  19726.789754  629753.18  629855.477740   
30559        NaN  615.0       97  19726.789754  629753.18  629853.864443   
30560        NaN  615.0       97  19726.789754  629753.18  629845.924773   
30561        NaN  615.0       97  19726.789754  629753.18  629832.157607   
30562        NaN  615.0       97  19726.789754  629753.18  629813.427988   
30563        NaN  615.0       97  19726.789754  629753.18  629790.912767   
30564        NaN  615.0       97  19726.789754  629753.18  629766.026656   
30565        NaN  615.0       97  19726.789754  629753.18  629740.333344   
30566        NaN  615.0       97  19726.789754  629753.

In [44]:
# calculate hydraulic confinement safety factor at each station point
#   required input data: reference maximum water pressure elevation (static or dynamic ??) 


buffer_all_df_sel = buffer_all_df.loc[(buffer_all_df["min_dist"] == "MIN"),]


dist = array(buffer_all_df_sel['dist'])
slope = array(buffer_all_df_sel['slope'])
z_align = array(buffer_all_df_sel['z_align'])
stat_sum = array(buffer_all_df_sel['stat_sum'])
stat_sum[0] = 0  #correction for station_stat_sum being for n-1 above (to be fixed above)

FS = (dist * density_rock * cos(slope*pi/180.)) / ((max_static_water_level - z_align) * 9.805)
print(FS)
print(stat_sum)

buffer_all_df_sel["FS"] = np.nan
for n in range(0, len(buffer_all_df_sel)):
    buffer_all_df_sel.iloc[n, buffer_all_df_sel.columns.get_loc("FS")] = FS[n]

buffer_all_df_sel = buffer_all_df_sel.drop(columns =["x_align", "y_align", "min_dist", "id_buffer_point"])
    

[5.14807827 5.19580535 5.27611293 5.40177498 5.48462261 5.54416686
 4.54829109 4.37555014 4.13389495 3.91514759 3.89028855 3.86103874
 3.8004861  3.7997747  3.87002425 4.16801308 4.18244143 4.01815365
 4.02456625 3.77990484 3.42046029 3.42170787 3.3581076  3.28518187
 3.15670118 3.3204253  3.37665063 3.76968881 3.93861408 3.96907514
 3.88872113 3.80863509 3.589688   3.48696328 3.42003118 3.26647894
 3.22363976 3.08127627 3.02585337 2.97703227 2.97691308 2.93338644
 3.06784429 2.96777519 2.80607215 2.57212522 2.47704812 2.60716716
 2.59432212 2.57675886 2.52426369 2.50759697 2.48458798 2.44572091
 2.40644825 2.41589565 2.41051231 2.40432006 2.32639442 2.35934059
 2.36094955 2.29482667 2.29071246 2.28122562 2.29485227 2.28807288
 2.32847936 2.3161504  2.2965867  2.24359075 2.22271279 2.23258223
 2.18447895 2.16890057 2.19907128 2.20250042 2.22011056 2.25310724
 2.26123692 2.27834392 2.3142967  2.33368579 2.29181898 2.27826795
 2.24932673 2.21734935 2.2183184  2.12760997 2.0715959  2.1025

In [45]:
dist = 103.2
z_align = 1099.3
slope = 0
FS = (dist * density_rock * cos(slope*pi/180.)) / ((max_static_water_level - z_align) * 9.805)
print(FS)
print(max_static_water_level)

1.4251832499026906
1298.7


In [46]:
#buffer_all_df_sel["stat_sum"]
#buffer_all_df_sel.iloc[1, buffer_all_df_sel.columns.get_loc("stat_sum")]
buffer_all_df_sel.iloc[1, buffer_all_df_sel.columns.get_loc("FS")]


5.195805348011214

In [47]:
buffer_all_df_sel
#buffer_all_df_sel.tail(9)

dist_stat           h id_point      stat_sum       x_buffer  \
164     49.38982  358.890000        0  15000.000000  634503.895000   
343     49.38982  365.685797        1  15049.389820  634477.734066   
527     49.38982  369.148261        2  15098.779641  634414.486169   
721     49.38982  372.610725        3  15148.169461  634353.193441   
910     49.38982  379.406522        4  15197.559282  634304.241866   
915     49.38982  379.535652        5  15246.949102  634231.400217   
1216    49.38982  376.331449        6  15296.338923  634051.412812   
1327    49.38982  369.793913        7  15345.728743  633958.435128   
1608    49.38982  359.923043        8  15395.118564  633985.482303   
1721    49.38982  330.052174        9  15444.508384  633924.167674   
1884    49.38982  310.181304       10  15493.898205  633897.242189   
2017    49.38982  300.310435       11  15543.288025  633886.943260   
2159    49.38982  280.439565       12  15592.677846  633858.455686   
2262    49.38982  280.568696       13  15642.067666  633863.777990   
2358    49.38982  290.697826       14  15691.457487  633843.734494   
2455    49.38982  310.826957       15  15740.847307  633834.556737   
2593    49.38982  324.289420       16  15790.237128  633791.863984   
2750    49.38982  326.085217       17  15839.626948  633569.068893   
2893    49.38982  331.214348       18  15889.016769  633540.015207   
2966    49.38982  311.343478       19  15938.406589  633390.667301   
3158    49.38982  301.472609       20  15987.796410  633390.528296   
3280    49.38982  281.601739       21  16037.186230  633357.204616   
3378    49.38982  251.730870       22  16086.576051  633326.675358   
3463    49.38982  231.860000       23  16135.965871  633317.554929   
3536    49.38982  231.989130       24  16185.355692  633293.333043   
3599    49.38982  242.118261       25  16234.745512  633301.528124   
3655    49.38982  262.247391       26  16284.135333  633280.919279   
3812    49.38982  277.376522       27  16333.525153  633169.238685   
3886    49.38982  282.505652       28  16382.914974  633178.472011   
4019    49.38982  282.634783       29  16432.304794  633002.278707   
4120    49.38982  277.763913       30  16481.694615  632941.953564   
4222    49.38982  272.893043       31  16531.084435  632902.812033   
4305    49.38982  263.022174       32  16580.474256  632821.865262   
4414    49.38982  253.151304       33  16629.864076  632805.138343   
4498    49.38982  248.280435       34  16679.253897  632775.349296   
4571    49.38982  238.409565       35  16728.643717  632726.942009   
4644    49.38982  233.538696       36  16778.033538  632678.046077   
4717    49.38982  233.667826       37  16827.423358  632628.661501   
4788    49.38982  223.796957       38  16876.813178  632580.254214   
4849    49.38982  218.926087       39  16926.202999  632527.318689   
4905    49.38982  219.055217       40  16975.592819  632528.831748   
4972    49.38982  217.878183       41  17024.982640  632479.323043   
5055    49.38982  216.925808       42  17074.372460  632381.154918   
5121    49.38982  211.109275       43  17123.762281  632332.412620   
5175    49.38982  204.571739       44  17173.152101  632261.602832   
5222    49.38982  194.700870       45  17222.541922  632191.621667   
5270     1.00000  184.830000       46  17271.931742  632148.555408   
5718    49.07716  599.515000       47  17272.931742  632152.046013   
6121    49.07716  584.424700       48  17322.008903  632069.641127   
6583    49.07716  589.334400       49  17371.086063  632060.794554   
7026    49.07716  594.244100       50  17420.163223  632011.341629   
7416    49.07716  589.153800       51  17469.240383  631888.113958   
7885    49.07716  589.063500       52  17518.317544  631889.830936   
8288    49.07716  578.973200       53  17567.394704  631783.917951   
8769    49.07716  578.882900       54  17616.471864  631796.649469   
9217    49.07716  582.935102       55  17665.549024  631770.061511   
9657    49.07716 

In [48]:
z_dtm_align = go.Scatter(
    x=alignment_stationed_df['distance_stat_sum'].tolist(),
    y=alignment_stationed_df['z_dtm_align'].tolist(),
    name = "Terrain",
    mode='lines',
    line=dict(width=0.5,
              color='rgb(196, 97, 26)'),
    fill='tonexty'
)
####print('z_dtm_align',z_dtm_align)

z_align_line = go.Scatter(
    x=alignment_stationed_df['distance_stat_sum'].tolist(),
    y=alignment_stationed_df['z_align'].tolist(),
    line=dict(width=3,
              color='rgb(0, 0, 0)'),
    name ="Tunnel"
)

data = [z_dtm_align, z_align_line]

layout = go.Layout(
    title='Longitudinal Section',
    showlegend=False,
    xaxis=dict(
        title= "Stationing",
    ),
    yaxis=dict(
        title = "m a.s.l.",
        #range = [300,800]  #need a procedure to automate this
    ),
    margin=dict(
        #l=50,
        b=40
    ),
    height=400,
)

fig = go.Figure(data=data, layout=layout)
plotly.offline.iplot(fig, show_link=False, filename='stacked-area-plot')



# initialize variables 
x_data = []
y_data = []
traces = []
annotations = []

fs = buffer_all_df_sel['FS'].tolist(),
c_fs = []
for i in range(len(buffer_all_df_sel.index)):
    if fs[0][i] <= 1.3:
        c_fs.append('red')
    elif 1.3 < fs[0][i] < 1.5:
        c_fs.append('yellow')
    else:
        c_fs.append('green')
slope = buffer_all_df_sel['slope'].tolist(),
c_slope = []
for i in range(len(buffer_all_df_sel.index)):
    if slope[0][i] > 30:
        c_slope.append('red')
    else:
        c_slope.append('green')        

x_data = [buffer_all_df_sel['dist_stat'].tolist()]
# x_data = [buffer_all_df_sel['dist_stat'].tolist(),
#           buffer_all_df_sel['dist_stat'].tolist()]

y_data = ['hydraulic confinement']
# y_data = ['slope',
#           'hydraulic confinement']

for i in range(0, len(x_data[0])):
    for xd, yd in zip(x_data, y_data):
        traces.append(go.Bar(
            x=[xd[i]],
            y=[yd],
            width = 0.3,
            orientation='h',
            marker=dict(
                color = c_fs[i],
            ),
            hoverinfo = 'none',
        ))
        
layout = go.Layout(
    xaxis=dict(
        showgrid=False,
        showline=False,
        showticklabels=False,
        zeroline=False,
        domain=[0.08, 1]  #horizontal extent of bar
    ),
    yaxis=dict(
        showgrid=False,
        showline=False,
        showticklabels=False,
        zeroline=False,
    ),
    barmode='stack',
    #paper_bgcolor='rgb(248, 248, 255)',
    #plot_bgcolor='rgb(248, 248, 255)',
    margin=dict(
        l=0,
        r=0,
        t=0,
        b=0
    ),
    showlegend=False,
    width=945,
    height=70,
)

for yd, xd in zip(y_data, x_data):
    # labeling the y-axis
    annotations.append(dict(xref='paper', yref='y',
                            x=0.09, y=yd, #x is position of text
                            xanchor='left',
                            text=str(yd),
                            font=dict(family='Arial', size=14,
                                      #color='rgb(67, 67, 67)'),
                                      color='white'),
                            showarrow=False, align='left'))
layout['annotations'] = annotations

fig = go.Figure(data=traces, layout=layout)
plotly.offline.iplot(fig, show_link=False, config=dict(displayModeBar=False), filename='bar-colorscale')

In [49]:
buffer_all_df_sel.loc[:, ['stat_sum', 'z_align', 'h', 'z_dtm_buffer', 'dist', 'slope', 'FS']].round(2).tail(200)

stat_sum  z_align       h  z_dtm_buffer    dist  slope    FS
164    15000.00  1111.11  358.89       1460.00  352.64   6.00  5.15
343    15049.39  1110.98  365.69       1465.86  358.70   9.09  5.20
527    15098.78  1110.85  369.15       1470.00  363.00   7.47  5.28
721    15148.17  1110.72  372.61       1480.00  370.24   5.14  5.40
910    15197.56  1110.59  379.41       1485.86  376.24   5.26  5.48
915    15246.95  1110.46  379.54       1490.00  379.54   3.09  5.54
1216   15296.34  1110.34  376.33       1440.00  356.01  29.08  4.55
1327   15345.73  1110.21  369.79       1390.00  335.37  26.74  4.38
1608   15395.12  1110.08  359.92       1410.00  317.06  26.74  4.13
1721   15444.51  1109.95  330.05       1370.00  294.18  24.18  3.92
1884   15493.90  1109.82  310.18       1370.00  279.97  17.62  3.89
2017   15543.29  1109.69  300.31       1360.00  269.58  10.56  3.86
2159   15592.68  1109.56  280.44       1370.00  261.95   4.77  3.80
2262   15642.07  1109.43  280.57       1370.00  262.07   4.77  3.80
2358   15691.46  1109.30  290.70       1370.00  267.10   4.77  3.87
2455   15740.85  1109.17  310.83       1380.00  289.97   8.39  4.17
2593   15790.24  1109.04  324.29       1390.00  301.03  16.88  4.18
2750   15839.63  1108.91  326.09       1390.00  301.37  23.23  4.02
2893   15889.02  1108.79  331.21       1380.00  292.82  18.58  4.02
2966   15938.41  1108.66  311.34       1350.00  287.19  24.72  3.78
3158   15987.80  1108.53  301.47       1350.00  261.55  25.42  3.42
3280   16037.19  1108.40  281.60       1340.00  246.53  16.43  3.42
3378   16086.58  1108.27  251.73       1330.00  234.24   7.51  3.36
3463   16135.97  1108.14  231.86       1330.00  229.31   7.51  3.29
3536   16185.36  1108.01  231.99       1330.00  229.44  17.69  3.16
3599   16234.75  1107.88  242.12       1340.00  239.88  16.43  3.32
3655   16284.14  1107.75  262.25       1330.00  245.76  17.69  3.38
3812   16333.53  1107.62  277.38       1370.00  263.84   7.51  3.77
3886   16382.91  1107.49  282.51       1370.00  275.85   7.51  3.94
4019   16432.30  1107.37  282.63       1380.00  278.43   7.91  3.97
4120   16481.69  1107.24  277.76       1375.00  273.47   8.61  3.89
4222   16531.08  1107.11  272.89       1370.00  268.50   9.27  3.81
4305   16580.47  1106.98  263.02       1350.00  255.51  12.00  3.59
4414   16629.86  1106.85  253.15       1350.00  248.37  12.00  3.49
4498   16679.25  1106.72  248.28       1345.00  240.29   7.13  3.42
4571   16728.64  1106.59  238.41       1335.00  230.35   8.38  3.27
4644   16778.03  1106.46  233.54       1330.00  225.44   3.37  3.22
4717   16827.42  1106.33  233.67       1325.00  220.61  12.65  3.08
4788   16876.81  1106.20  223.80       1320.00  215.62  11.19  3.03
4849   16926.20  1106.07  218.93       1310.00  211.14   9.50  2.98
4905   16975.59  1105.94  219.06       1310.00  211.28   9.50  2.98
4972   17024.98  1105.82  217.88       1310.00  211.32  13.52  2.93
5055   17074.37  1105.69  216.93       1320.00  216.02   5.49  3.07
5121   17123.76  1105.56  211.11       1313.33  209.44   6.36  2.97
5175   17173.15  1105.43  204.57       1300.00  201.18  11.77  2.81
5222   17222.54  1105.30  194.70       1280.00  186.37  14.23  2.57
5270   17271.93  1105.17  184.83       1270.00  175.97   8.38  2.48
5718   17272.93   690.48  599.52       1270.00  582.07   8.38  2.61
6121   17322.01   685.58  584.42       1256.67  580.89   6.07  2.59
6583   17371.09   680.67  589.33       1256.67  581.58   6.07  2.58
7026   17420.16   675.76  594.24       1250.00  579.93  10.05  2.52
7416   17469.24   670.85  589.15       1230.00  574.96   6.07  2.51
7885   17518.32   665.94  589.06       1230.00  574.14   6.07  2.48
8288   17567.39   661.03  578.97       1220.00  574.25   9.51  2.45
8769   17616.47   656.12  578.88       1220.00  569.38   9.51  2.41
9217   17665.55   651.21  582.94       1220.00  571.26   6.06  2.42
9657   17714.63   646.30  578.70       1220.00  574.31   6.06  2.41
10084  17763.70   641.39  581.95       1215.86  576.90   5.83  

In [50]:
alignment_stationed_line_plot = go.Scatter(
    x=alignment_stationed_df['x_align'].tolist(),
    y=alignment_stationed_df['y_align'].tolist(),
    line=dict(width=3,
              color='rgb(0, 0, 0)'),
    name ="alignment_stationed_line"
)

alignment_point_plot = go.Scatter(
    x=alignment_df['Easting'].tolist(),
    y=alignment_df['Northing'].tolist(),
    name ="alignment_point",
    mode = "markers",
    marker = dict(
        size = 20,
        color = 'rgb(255, 153, 153)'
    )
)

alignment_stationed_point_plot = go.Scatter(
    x=alignment_stationed_df['x_align'].tolist(),
    y=alignment_stationed_df['y_align'].tolist(),
    mode = "markers",
    name ="alignment_stationed_point",
    marker = dict(
        size = 6,
        color = 'rgb(255, 0, 0)'
    )
)

buffer_all_df_point_plot = go.Scatter(
    x=buffer_all_df['x_buffer'].tolist(),
    y=buffer_all_df['y_buffer'].tolist(),
    mode = "markers",
    name ="buffer_all_point",
     marker = dict(
        size = 6,
        color = 'rgba(0, 0, 153, 0.005)'  #use for high resolution
        #color = 'rgba(0, 0, 153, 0.4)'  #use for low resolution
    )
)
buffer_min_df_point_plot = go.Scatter(
    x=buffer_all_df_sel['x_buffer'].tolist(),
    y=buffer_all_df_sel['y_buffer'].tolist(),
    mode = "markers",
    name ="buffer_min",
     marker = dict(
        size = 8,
        color = 'rgb(0, 0, 153)'
    )
)

data = [alignment_stationed_line_plot, alignment_point_plot, alignment_stationed_point_plot, 
        buffer_all_df_point_plot, buffer_min_df_point_plot]


fig = go.Figure(data=data)
plotly.offline.iplot(fig, show_link=False, filename='stacked-area-plot')

ToDo: check that grid width is adequate (display grid points on graphic very light)
ToDo: overlay project layout as basemap (opague)

In [51]:
alignment_df.head(20)

Station    Northing    Easting  Elevation  distance_intermed_align
0  15000.000  6038563.42  634478.26   1111.110              2271.931742
1  17271.925  6038624.52  632207.15   1105.170                 1.000000
2  17271.925  6038624.52  632206.15    690.485              2453.858012
3  19726.777  6038690.53  629753.18    445.000                      NaN